In [22]:
!pip install numpy pandas scikit-learn pykrige matplotlib

Defaulting to user installation because normal site-packages is not writeable


In [23]:
import numpy as np
import pandas as pd
from pykrige.ok import OrdinaryKriging
from pykrige.uk import UniversalKriging
import matplotlib.pyplot as plt
from scipy import stats
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, r2_score
import folium
from folium.plugins import MarkerCluster

In [24]:
# Load the data
data = pd.read_excel('Dataset.xlsx')

row_count = data.shape[0]
print("Number of rows:", row_count)

print("\n", data.head(5))

# Extract coordinates and variables
X = data['Longitude'].values
Y = data['Latitude'].values
Z = data['LungCancerRate'].values

Number of rows: 3143

    FIPS   Parish   Latitude  Longitude    Income  Insurance    PM 2.5  \
0  1001  Autauga  32.535142 -86.642900  0.308876   0.828652  0.619048   
1  1003  Baldwin  30.727825 -87.722745  0.343421   0.772472  0.455782   
2  1005  Barbour  31.870090 -85.391068  0.151268   0.719101  0.578231   
3  1007     Bibb  32.998376 -87.126814  0.231939   0.755618  0.605442   
4  1009   Blount  33.980871 -86.567006  0.251355   0.707865  0.591837   

    Poverty   Smoking  LungCancerRate  
0  0.161165  0.424242        0.311271  
1  0.135922  0.478788        0.288991  
2  0.403883  0.515152        0.338794  
3  0.316505  0.590909        0.412844  
4  0.198058  0.578788        0.333552  


In [25]:
# Handle zero values
Z_positive = np.where(Z == 0, 0.01, Z)

# Log transform the target variable
Z_log = np.log1p(Z_positive)

# Prepare additional variables
smoking = data['Smoking'].values
poverty = data['Poverty'].values
pm25 = data['PM 2.5'].values
uninsured = data['Insurance'].values
income = data['Income'].values

# Split the data into training and testing sets
X_train, X_test, Y_train, Y_test, Z_train, Z_test, smoking_train, smoking_test, poverty_train, poverty_test, pm25_train, pm25_test, uninsured_train, uninsured_test, income_train, income_test = train_test_split(
    X, Y, Z_log, smoking, poverty, pm25, uninsured, income, test_size=0.2, random_state=42)

In [26]:
# Perform Ordinary Kriging and store the predicted values
ok_model = OrdinaryKriging(X_train, Y_train, Z_train, variogram_model='spherical')
ok_all_predictions, _ = ok_model.execute('points', X, Y)
ok_all_predictions = np.expm1(ok_all_predictions)
data['OK_Predicted_LungCancerRate'] = ok_all_predictions

In [27]:
# Calculate p-values
def calculate_p_values(pred, actual):
    t_statistic = (pred - actual.mean()) / (pred.std() / np.sqrt(len(pred)))
    p_values = 2 * (1 - stats.t.cdf(np.abs(t_statistic), df=len(pred)-1))
    return p_values

ok_p_values = calculate_p_values(data['OK_Predicted_LungCancerRate'], data['LungCancerRate'])

data['OK_P_Value'] = ok_p_values
print(data.head(5))

   FIPS   Parish   Latitude  Longitude    Income  Insurance    PM 2.5  \
0  1001  Autauga  32.535142 -86.642900  0.308876   0.828652  0.619048   
1  1003  Baldwin  30.727825 -87.722745  0.343421   0.772472  0.455782   
2  1005  Barbour  31.870090 -85.391068  0.151268   0.719101  0.578231   
3  1007     Bibb  32.998376 -87.126814  0.231939   0.755618  0.605442   
4  1009   Blount  33.980871 -86.567006  0.251355   0.707865  0.591837   

    Poverty   Smoking  LungCancerRate  OK_Predicted_LungCancerRate  \
0  0.161165  0.424242        0.311271                     0.318862   
1  0.135922  0.478788        0.288991                     0.288991   
2  0.403883  0.515152        0.338794                     0.338794   
3  0.316505  0.590909        0.412844                     0.412844   
4  0.198058  0.578788        0.333552                     0.333552   

     OK_P_Value  
0  8.500124e-01  
1  0.000000e+00  
2  0.000000e+00  
3  0.000000e+00  
4  3.108624e-15  


In [28]:
# Calculate MAE and R-squared for the entire dataset
ok_mae = mean_absolute_error(data['LungCancerRate'], data['OK_Predicted_LungCancerRate'])
ok_r2 = r2_score(data['LungCancerRate'], data['OK_Predicted_LungCancerRate'])

# Display error metrics
print(f"Ordinary Kriging - MAE: {ok_mae:.4f}")
print(f"Ordinary Kriging - R-squared: {ok_r2:.4f}")

Ordinary Kriging - MAE: 0.0118
Ordinary Kriging - R-squared: 0.8971


In [29]:
# Plotting the results on an interactive map
m = folium.Map(location=[31.0, -92.0], zoom_start=4)

marker_cluster = MarkerCluster().add_to(m)
for idx, row in data.iterrows():
    folium.Marker(
        location=(row['Latitude'], row['Longitude']),
        popup=(
            f"<strong>Parish:</strong> {row['Parish']}<br>"
            f"<strong>Predicted Lung Cancer Rate:</strong> {row['OK_Predicted_LungCancerRate']:.2f}"
        ),
        icon=folium.Icon(color='red')
    ).add_to(marker_cluster)

# Displaying the map
m